# Training Emely

This notebook is for training Emely with different configurations.
Use the blender_opts dictionary for the standard options. 

### Configuration

#### Base Config
We'll call the base configuration "Blender base config" and it's the blender 90M model fine tuned on the internal and external tasks

### Required config for a run

- task
- multitask_weights
- model_file

### Optional config
- mutators
- lr


### Different mutators for different tasks?
--task internal:mutators=word_shuffle,internal:mutators=last_turn


### Evaluation
All models are evaluated on the internal and external tasks

In [1]:
from parlai.scripts.train_model import TrainModel
from pathlib import Path
from copy import deepcopy
import shutil

In [2]:
blender_opts = {'init_model': 'zoo:blender/blender_90M/model',
                'dict_file': 'zoo:blender/blender_90M/model.dict',
              'model': 'transformer/generator',
              'embedding_size': 512,
              'n_layers': 8,
              'ffn_size': 2048,
              'dropout': 0.1,
              'n_heads': 16,
              'learn_positional_embeddings': True,
              'n_positions': 512,
              'variant': 'xlm',
              'activation': 'gelu',
              'fp16': True,
              'text_truncate': 512,
              'label_truncate': 128,
              'dict_tokenizer': 'bpe',
              'optimizer': 'adamax',
              'lr_scheduler': 'reduceonplateau',
              'betas': '0.9,0.999',
              'update_freq': 1,
              'attention_dropout': 0.0,
              'relu_dropout': 0.0,
              'dict_lower': True,
              'lr': 1e-06,
              'gradient_clip': 0.1,
              'veps': 0.25,
              'skip_generation': False,
              'vp': 15,
              'stim': 60,
              'vme': 20000,
              'bs': 16,
              'vmt': 'ppl',
              'vmm': 'min',
              'save_after_valid': True,
              'wblog': True,
              'wandb_project': 'parlaiemely',
              'tensorboard_log': True,
              'metrics': 'ppl,bleu-4,rouge-L',
              'evaltask': 'internal,external',
              'inference': 'beam',
              'beam_size': 10,
              'beam_min_length': 10,
              'beam_block_ngram': 3
               }

#              'dict_file': 'zoo:blender/blender_90M/model.dict'

In [3]:
def run_training(tasks, weights, mutators=None):

    # Set name for file and model run on wandb
    if mutators is not None:
        name = f'blender-{tasks}-{weights}-{mutators}'

    else:
        name = f'blender-{tasks}-{weights}'

        
    #%env WANDB_NAME=$name
    mf = Path.cwd().parents[1].joinpath(f'models/model-runs/{name}/model')
    
    if mutators is not None:
        run_opts = {'task': tasks,
                    'multitask_weights': weights,
                    'model_file': mf.as_posix(),
                    'mutators': mutators
                    }        
    else:
        run_opts = {'task': tasks,
                    'multitask_weights': weights,
                    'model_file': mf.as_posix()
                   }
    
    # Copy the standard opts and update them
    opts = deepcopy(blender_opts)
    opts.update(run_opts)

    TrainModel.main(**opts)

## 0. Test run 2 after each other

In [ ]:
name = 'TEST'
mf = Path.cwd().parents[1].joinpath(f'models/model-runs/{name}/model')

if mf.parent.exists():
    shutil.rmtree(mf.parent)

tasks = 'internal,external'
weights='5,1'
mutators='word_shuffle'
run_training(tasks=tasks,weights=weights, mutators=mutators)

## 1. Blender base config

### Datasets with sampling weights:
- internal - 6
- external - 3

### Mutators
None

In [4]:
tasks='internal,external'
weights= '6,3'

run_training(tasks=tasks,weights=weights)

18:25:42 | building dictionary first...
18:25:42 | No model with opt yet at: /home/alex/ParlaiEmely/models/model-runs/blender-internal,external-6,3/model(.opt)
18:25:42 | your model is being loaded with opts that do not exist in the model you are initializing the weights with: allow_missing_init_opts: False,download_path: None,loglevel: info,dynamic_batching: None,verbose: False,is_debug: False,datapath: /home/alex/ParlaiEmely/ParlAI/data,eval_dynamic_batching: None,num_workers: 0,max_train_steps: -1,log_every_n_steps: 50,validation_every_n_steps: -1,load_from_checkpoint: True,tensorboard_logdir: None,wandb_log: True,wandb_name: None,wandb_project: parlaiemely,wandb_entity: None,mutators: None,n_encoder_layers: -1,n_decoder_layers: -1,model_parallel: False,beam_block_full_context: True,beam_delay: 30,beam_block_list_filename: None,temperature: 1.0,interactive_mode: False,history_reversed: False,history_add_global_end_token: None,special_tok_lst: None,bpe_vocab: None,bpe_merge: None,bpe

18:25:46 |     tensorboard_logdir: None
18:25:46 |     text_truncate: 512
18:25:46 |     topk: 10
18:25:46 |     topp: 0.9
18:25:46 |     truncate: -1
18:25:46 |     update_freq: 1
18:25:46 |     use_reply: label
18:25:46 |     validation_cutoff: 1.0
18:25:46 |     validation_every_n_epochs: 0.25
18:25:46 |     validation_every_n_secs: -1
18:25:46 |     validation_every_n_steps: -1
18:25:46 |     validation_max_exs: 20000
18:25:46 |     validation_metric: ppl
18:25:46 |     validation_metric_mode: min
18:25:46 |     validation_patience: 15
18:25:46 |     validation_share_agent: False
18:25:46 |     variant: xlm
18:25:46 |     verbose: False
18:25:46 |     wandb_entity: None
18:25:46 |     wandb_log: True
18:25:46 |     wandb_name: None
18:25:46 |     wandb_project: parlaiemely
18:25:46 |     warmup_rate: 0.0001
18:25:46 |     warmup_updates: -1
18:25:46 |     weight_decay: None
18:25:46 | Current ParlAI commit: e3c1edbef397de2c084a521fb0bb81489a432c74
18:25:46 | creating task(s): inter

wandb: W&B API key is configured (use `wandb login --relogin` to force relogin)


18:26:09 | training...
18:26:11 | time:25s total_exs:256 total_steps:16 epochs:0.26
             clen  clip  ctpb  ctps  ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gnorm  gpu_mem  llen  loss    lr  ltpb  \
   all      55.46     1 884.4  7331       0          0 132.6  256             32768  12.56    .1370 15.49 2.844 1e-06 245.9   
   external 56.23                         0          0         97                                   15.99 3.041               
   internal 54.69                         0          0        159                                   14.99 2.647               
             ltps  ltrunc  ltrunclen   ppl  token_acc  token_em  total_train_updates  tpb  tps   ups  
   all       2038       0          0 17.51      .4114         0                   16 1130 9370 8.348  
   external             0          0 20.92      .3830         0                                       
   internal             0          0 14.11      .4398         0

18:26:11 | creating task(s): inter

18:27:16 | running eval: valid
18:27:31 | eval completed in 15.48s
18:27:31 | valid:
             accuracy  bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss    lr  ltpb  ltps  \
   all              0 .007787 53.69 635.2 512.6       0          0 11.39  171 .1783   .06922 14.68 2.767 1e-06   190 153.3   
   external         0 .009779 62.36                   0          0         44 .1576          15.89 3.042                     
   internal         0 .005794 45.02                   0          0        127 .1990          13.46 2.492                     
             ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all            0          0 16.52    .1777      .4361         0                   64 825.2 665.9  
   external       0          0 20.96    .1570      .4049         0                                   
   internal       0          0 12.09    .1984      .4673         0

18:27:31 | saving model checkpoint: /

...

19:54:12 | running eval: valid
19:54:24 | eval completed in 11.94s
19:54:24 | valid:
             accuracy  bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss        lr  ltpb  \
   all              0  .01421 53.69 635.2 650.3       0          0 14.45  171 .2296   .06918 14.68 2.489 1.562e-08   190   
   external         0  .01279 62.36                   0          0         44 .1960          15.89 2.766                   
   internal         0  .01564 45.02                   0          0        127 .2632          13.46 2.213                   
             ltps  ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all      194.5       0          0 12.51    .2351      .4743         0                 5120 825.2 844.8  
   external             0          0 15.89    .1951      .4363         0                                   
   internal             0          0 9.139    .2751      .5123         0

19:54:24 | saving mod

19:55:15 | running eval: valid
19:55:27 | eval completed in 11.99s
19:55:27 | valid:
             accuracy  bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss        lr  ltpb  \
   all              0  .01532 53.69 635.2 648.3       0          0  14.4  171 .2278   .06902 14.68 2.489 1.562e-08   190   
   external         0  .01501 62.36                   0          0         44 .1921          15.89 2.766                   
   internal         0  .01564 45.02                   0          0        127 .2636          13.46 2.213                   
             ltps  ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all      193.9       0          0 12.52    .2350      .4743         0                 5184 825.2 842.2  
   external             0          0 15.89    .1943      .4363         0                                   
   internal             0          0 9.139    .2757      .5123         0

19:55:27 | saving mod

19:56:02 | running eval: valid
19:56:14 | eval completed in 12.07s
19:56:14 | valid:
             accuracy  bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss        lr  ltpb  \
   all              0  .01532 53.69 635.2 645.1       0          0 14.33  171 .2283   .06903 14.68 2.489 1.562e-08   190   
   external         0  .01501 62.36                   0          0         44 .1921          15.89 2.766                   
   internal         0  .01564 45.02                   0          0        127 .2645          13.46 2.213                   
             ltps  ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all        193       0          0 12.52    .2356      .4756         0                 5232 825.2 838.1  
   external             0          0 15.89    .1943      .4378         0                                   
   internal             0          0 9.139    .2770      .5135         0

19:56:14 | saving mod

19:57:03 | running eval: valid
19:57:15 | eval completed in 11.88s
19:57:15 | valid:
             accuracy  bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss        lr  ltpb  \
   all              0  .01532 53.69 635.2 655.2       0          0 14.56  171 .2287   .06922 14.68 2.489 1.562e-08   190   
   external         0  .01501 62.36                   0          0         44 .1921          15.89 2.766                   
   internal         0  .01564 45.02                   0          0        127 .2653          13.46 2.212                   
             ltps  ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all        196       0          0 12.52    .2355      .4746         0                 5296 825.2 851.2  
   external             0          0 15.89    .1943      .4363         0                                   
   internal             0          0 9.138    .2768      .5129         0

19:57:15 | saving mod

19:58:05 | running eval: valid
19:58:17 | eval completed in 11.93s
19:58:17 | valid:
             accuracy  bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss        lr  ltpb  \
   all              0  .01532 53.69 635.2   653       0          0 14.51  171 .2286   .06918 14.68 2.489 1.562e-08   190   
   external         0  .01501 62.36                   0          0         44 .1921          15.89 2.766                   
   internal         0  .01564 45.02                   0          0        127 .2652          13.46 2.213                   
             ltps  ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all      195.3       0          0 12.52    .2355      .4743         0                 5360 825.2 848.3  
   external             0          0 15.89    .1943      .4363         0                                   
   internal             0          0 9.139    .2768      .5123         0

19:58:17 | saving mod

## 2. Blender base config + bst

### Datasets with sampling weights:
- internal: 6
- external: 3
- blended_skill_talk: 1

### Mutators
None

In [5]:
tasks='internal,external,blended_skill_talk'
weights= '6,3,1'

run_training(tasks=tasks,weights=weights)

19:59:12 | building dictionary first...
19:59:12 | No model with opt yet at: /home/alex/ParlaiEmely/models/model-runs/blender-internal,external,blended_skill_talk-6,3,1/model(.opt)
19:59:12 | your model is being loaded with opts that do not exist in the model you are initializing the weights with: allow_missing_init_opts: False,download_path: None,loglevel: info,dynamic_batching: None,verbose: False,is_debug: False,datapath: /home/alex/ParlaiEmely/ParlAI/data,eval_dynamic_batching: None,num_workers: 0,max_train_steps: -1,log_every_n_steps: 50,validation_every_n_steps: -1,load_from_checkpoint: True,tensorboard_logdir: None,wandb_log: True,wandb_name: None,wandb_project: parlaiemely,wandb_entity: None,mutators: None,n_encoder_layers: -1,n_decoder_layers: -1,model_parallel: False,beam_block_full_context: True,beam_delay: 30,beam_block_list_filename: None,temperature: 1.0,interactive_mode: False,history_reversed: False,history_add_global_end_token: None,special_tok_lst: None,bpe_vocab: Non

19:59:13 |     text_truncate: 512
19:59:13 |     topk: 10
19:59:13 |     topp: 0.9
19:59:13 |     truncate: -1
19:59:13 |     update_freq: 1
19:59:13 |     use_reply: label
19:59:13 |     validation_cutoff: 1.0
19:59:13 |     validation_every_n_epochs: 0.25
19:59:13 |     validation_every_n_secs: -1
19:59:13 |     validation_every_n_steps: -1
19:59:13 |     validation_max_exs: 20000
19:59:13 |     validation_metric: ppl
19:59:13 |     validation_metric_mode: min
19:59:13 |     validation_patience: 15
19:59:13 |     validation_share_agent: False
19:59:13 |     variant: xlm
19:59:13 |     verbose: False
19:59:13 |     wandb_entity: None
19:59:13 |     wandb_log: True
19:59:13 |     wandb_name: None
19:59:13 |     wandb_project: parlaiemely
19:59:13 |     warmup_rate: 0.0001
19:59:13 |     warmup_updates: -1
19:59:13 |     weight_decay: None
19:59:13 | Current ParlAI commit: adb7ed134aec01437ef8d4e6bf450827fd0fbdc2
19:59:14 | creating task(s): internal,external,blended_skill_talk
19:59:14

19:59:31 | training...
19:59:36 | time:22s total_exs:800 total_steps:50 epochs:0.03
                       clen  clip  ctpb  ctps  ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gnorm  gpu_mem  llen  loss  \
   all                76.17     1  1205 11381       0          0 151.1  800             32768  12.01    .3383 15.81 2.639   
   blended_skill_talk 78.69                         0          0        153                                   18.32 2.265   
   external           77.32                         0          0        271                                   15.11 3.002   
   internal           72.49                         0          0        376                                      14 2.651   
                         lr  ltpb  ltps  ltrunc  ltrunclen   ppl  token_acc  token_em  total_train_updates  tpb   tps   ups  
   all                1e-06 243.2  2297       0          0 14.64      .4411   .002179                   50 1448 13678 9.498  
   blended_skill_talk                  

20:00:14 | saving model checkpoint: /home/alex/ParlaiEmely/models/model-runs/blender-internal,external,blended_skill_talk-6,3,1/model.checkpoint
20:00:14 | Saving dictionary to /home/alex/ParlaiEmely/models/model-runs/blender-internal,external,blended_skill_talk-6,3,1/model.checkpoint.dict
20:00:20 | time:66s total_exs:6400 total_steps:400 epochs:0.23
                       clen  clip  ctpb  ctps  ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gnorm  gpu_mem  llen  loss  \
   all                81.76     1  1311  8837       0          0 107.8  800             24576    inf    .3406 15.36 2.606   
   blended_skill_talk 78.21                         0          0        208                                    17.2 2.484   
   external           84.54                         0          0        211                                   14.37  2.81   
   internal           82.53                         0          0        381                                   14.51 2.525   
                     

20:00:24 | time:70s total_exs:7008 total_steps:438 epochs:0.25
                       clen  clip  ctpb  ctps  ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gnorm  gpu_mem  llen  loss  \
   all                78.92     1  1274 11527       0          0 144.7  608             16384  11.44    .3338  15.6 2.535   
   blended_skill_talk 78.87                         0          0        141                                    18.9 2.269   
   external            75.7                         0          0        166                                   14.18 2.814   
   internal           82.19                         0          0        301                                   13.71 2.522   
                         lr  ltpb  ltps  ltrunc  ltrunclen   ppl  token_acc  token_em  total_train_updates  tpb   tps   ups  
   all                1e-06 240.7  2176       0          0 12.93      .4539         0                  438 1515 13704 9.047  
   blended_skill_talk                         0          0  

...

20:36:59 | time:2265s total_exs:232864 total_steps:14554 epochs:8.32
                       clen  clip  ctpb  ctps  ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gnorm  gpu_mem  llen  loss  \
   all                 87.8     1  1404 12894       0          0 146.9  800              8192  10.41    .3627 15.52 1.943   
   blended_skill_talk 83.38                         0          0        254                                   17.26 2.293   
   external            90.8                         0          0        184                                   15.02 1.782   
   internal           89.22                         0          0        362                                   14.28 1.753   
                            lr  ltpb  ltps  ltrunc  ltrunclen   ppl  token_acc  token_em  total_train_updates  tpb   tps   ups  
   all                1.25e-07 246.3  2263       0          0 7.206      .5495   .002762                14554 1650 15157 9.188  
   blended_skill_talk                           

20:37:38 | time:2304s total_exs:238272 total_steps:14892 epochs:8.51
                       clen  clip  ctpb  ctps  ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gnorm  gpu_mem  llen  loss  \
   all                78.99     1  1269 12141       0          0 153.1  608              8192  10.54    .3219 15.01 1.996   
   blended_skill_talk 79.91                         0          0        159                                   15.55 2.339   
   external           76.28                         0          0        169                                   15.22 1.796   
   internal           80.79                         0          0        280                                   14.26 1.854   
                            lr  ltpb  ltps  ltrunc  ltrunclen   ppl  token_acc  token_em  total_train_updates  tpb   tps  ups  
   all                1.25e-07 237.9  2276       0          0 7.595      .5399   .007516                14892 1507 14417 9.57  
   blended_skill_talk                            0

20:38:29 | time:2355s total_exs:243072 total_steps:15192 epochs:8.69
                       clen  clip  ctpb  ctps  ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gnorm  gpu_mem  llen  loss  \
   all                 86.2     1  1382 12170       0          0 140.9  800              8192  10.65    .3478 15.92 1.957   
   blended_skill_talk 86.63                         0          0        223                                   18.93 2.433   
   external           84.81                         0          0        216                                   15.02 1.773   
   internal           87.17                         0          0        361                                   13.81 1.667   
                            lr  ltpb  ltps  ltrunc  ltrunclen   ppl  token_acc  token_em  total_train_updates  tpb   tps   ups  
   all                1.25e-07   249  2193       0          0 7.524      .5472   .001543                15192 1631 14363 8.808  
   blended_skill_talk                           

20:39:18 | time:2404s total_exs:247680 total_steps:15480 epochs:8.85
                       clen  clip  ctpb  ctps  ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gnorm  gpu_mem  llen  loss  \
   all                83.17     1  1307 12574       0          0 153.9  800             16384  10.69    .3727 16.13 2.038   
   blended_skill_talk 91.64                         0          0        184                                   19.41 2.485   
   external           80.38                         0          0        261                                   14.33 1.803   
   internal           77.48                         0          0        355                                   14.64 1.825   
                            lr  ltpb  ltps  ltrunc  ltrunclen   ppl  token_acc  token_em  total_train_updates  tpb   tps   ups  
   all                1.25e-07 250.2  2407       0          0 8.091      .5336   .005972                15480 1557 14981 9.623  
   blended_skill_talk                           

20:39:52 | running eval: valid
20:40:04 | eval completed in 12.33s
20:40:04 | valid:
             accuracy  bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss       lr  ltpb  ltps  \
   all              0  .02351 53.69 635.2 624.8       0          0 13.88  171 .2377    .2007 14.68 2.487 1.25e-07   190 186.9   
   external         0  .02524 62.36                   0          0         44 .2036          15.89 2.774                        
   internal         0  .02178 45.02                   0          0        127 .2717          13.46   2.2                        
             ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all            0          0 12.53    .2437      .4788         0                15768 825.2 811.7  
   external       0          0 16.03    .2032      .4435         0                                   
   internal       0          0 9.026    .2841      .5140         0

20:40:04 | saving model c

## 3. Blender base + otter

### Datasets with sampling weights:
- internal: 6
- external: 3
- otter: 1

### Mutators
None

In [6]:
tasks='internal,external,otter'
weights= '6,3,1'

run_training(tasks=tasks,weights=weights)

20:41:00 | building dictionary first...
20:41:00 | No model with opt yet at: /home/alex/ParlaiEmely/models/model-runs/blender-internal,external,otter-6,3,1/model(.opt)
20:41:00 | your model is being loaded with opts that do not exist in the model you are initializing the weights with: allow_missing_init_opts: False,download_path: None,loglevel: info,dynamic_batching: None,verbose: False,is_debug: False,datapath: /home/alex/ParlaiEmely/ParlAI/data,eval_dynamic_batching: None,num_workers: 0,max_train_steps: -1,log_every_n_steps: 50,validation_every_n_steps: -1,load_from_checkpoint: True,tensorboard_logdir: None,wandb_log: True,wandb_name: None,wandb_project: parlaiemely,wandb_entity: None,mutators: None,n_encoder_layers: -1,n_decoder_layers: -1,model_parallel: False,beam_block_full_context: True,beam_delay: 30,beam_block_list_filename: None,temperature: 1.0,interactive_mode: False,history_reversed: False,history_add_global_end_token: None,special_tok_lst: None,bpe_vocab: None,bpe_merge: 

20:41:01 |     topp: 0.9
20:41:01 |     truncate: -1
20:41:01 |     update_freq: 1
20:41:01 |     use_reply: label
20:41:01 |     validation_cutoff: 1.0
20:41:01 |     validation_every_n_epochs: 0.25
20:41:01 |     validation_every_n_secs: -1
20:41:01 |     validation_every_n_steps: -1
20:41:01 |     validation_max_exs: 20000
20:41:01 |     validation_metric: ppl
20:41:01 |     validation_metric_mode: min
20:41:01 |     validation_patience: 15
20:41:01 |     validation_share_agent: False
20:41:01 |     variant: xlm
20:41:01 |     verbose: False
20:41:01 |     wandb_entity: None
20:41:01 |     wandb_log: True
20:41:01 |     wandb_name: None
20:41:01 |     wandb_project: parlaiemely
20:41:01 |     warmup_rate: 0.0001
20:41:01 |     warmup_updates: -1
20:41:01 |     weight_decay: None
20:41:01 | Current ParlAI commit: adb7ed134aec01437ef8d4e6bf450827fd0fbdc2
20:41:01 | creating task(s): internal,external,otter
20:41:01 | Loading ParlAI text data: /home/alex/ParlaiEmely/ParlAI/data/interna

20:41:19 | training...
20:41:22 | time:20s total_exs:384 total_steps:24 epochs:0.25
             clen  clip  ctpb  ctps  ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gnorm  gpu_mem  llen  loss    lr  ltpb  \
   all      67.27     1  1003  8595 .001449      .1261 137.1  384             19797    inf    .4639 19.63  3.08 1e-06 258.8   
   external 63.37                         0          0        120                                   16.95 2.974               
   internal 60.45                   .004348      .3783        230                                   14.13 2.668               
   otter       78                         0          0         34                                   27.82 3.597               
             ltps  ltrunc  ltrunclen   ppl  token_acc  token_em  total_train_updates  tpb   tps   ups  
   all       2218  .01961      .1667 23.49      .3821         0                   24 1262 10813 8.617  
   external             0          0 19.57      .3800         0          

20:41:22 | creating task(s): internal
20:41:22 | Loading ParlAI text data: /home/alex/ParlaiEmely/ParlAI/data/internal/valid.txt
20:41:22 | creating task(s): external
20:41:22 | Loading ParlAI text data: /home/alex/ParlaiEmely/ParlAI/data/external/valid.txt
20:41:22 | running eval: valid
20:41:39 | eval completed in 16.90s
20:41:39 | valid:
             accuracy    bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss    lr  ltpb  ltps  \
   all              0    .00489 53.69 635.2 478.2       0          0 10.62  171 .1656    .2003 14.68 2.808 1e-06   190   143   
   external         0   .009779 62.36                   0          0         44 .1546          15.89 3.079                     
   internal         0 1.784e-06 45.02                   0          0        127 .1766          13.46 2.538                     
             ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all            0          0 17.19    .16

20:42:27 | running eval: valid
20:42:42 | eval completed in 15.24s
20:42:42 | valid:
             accuracy  bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss    lr  ltpb  ltps  \
   all              0  .01258 53.69 635.2 523.4       0          0 11.63  171 .1901    .1934 14.68 2.749 1e-06   190 156.5   
   external         0  .01791 62.36                   0          0         44 .1771          15.89 3.026                     
   internal         0 .007253 45.02                   0          0        127 .2030          13.46 2.472                     
             ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all            0          0 16.23    .1879      .4342         0                   96 825.2 679.9  
   external       0          0 20.62    .1801      .3977         0                                   
   internal       0          0 11.85    .1957      .4708         0

20:42:42 | saving model checkpoint: /

...

21:55:59 | saving model checkpoint: /home/alex/ParlaiEmely/models/model-runs/blender-internal,external,otter-6,3,1/model.checkpoint
21:56:00 | did not beat best ppl: 12.4894 impatience: 2
21:56:00 | saving model checkpoint: /home/alex/ParlaiEmely/models/model-runs/blender-internal,external,otter-6,3,1/model.checkpoint
21:56:04 | time:4503s total_exs:97152 total_steps:6072 epochs:63.83
             clen  clip  ctpb  ctps  ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gnorm  gpu_mem  llen  loss        lr  \
   all      62.54     1  1025  9650       0          0 150.6  384              8192  10.01    .4273 18.98 2.663 1.562e-08   
   external 66.23                         0          0        123                                   16.02 2.359             
   internal    64                         0          0        224                                   14.76 2.132             
   otter    57.38                         0          0         37                                   26.16 3.499 

21:56:53 | running eval: valid
21:57:05 | eval completed in 11.82s
21:57:05 | valid:
             accuracy  bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss        lr  ltpb  \
   all              0  .02339 53.69 635.2 652.5       0          0 14.49  171 .2399    .2004 14.68 2.487 1.562e-08   190   
   external         0  .02897 62.36                   0          0         44 .2120          15.89 2.765                   
   internal         0   .0178 45.02                   0          0        127 .2677          13.46 2.209                   
             ltps  ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all      195.2       0          0 12.49    .2427      .4750         0                 6144 825.2 847.6  
   external             0          0 15.88    .2071      .4378         0                                   
   internal             0          0 9.106    .2783      .5123         0

21:57:05 | saving mod

21:57:55 | saving model checkpoint: /home/alex/ParlaiEmely/models/model-runs/blender-internal,external,otter-6,3,1/model.checkpoint
21:57:56 | did not beat best ppl: 12.4894 impatience: 9
21:57:59 | time:4617s total_exs:99840 total_steps:6240 epochs:65.60
             clen  clip  ctpb  ctps  ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gnorm  gpu_mem  llen  loss        lr  \
   all      62.98     1  1008  9700       0          0   154  384              8192  10.23    .3946 21.56 2.532 1.562e-08   
   external 59.84                         0          0        130                                    15.3 2.283             
   internal 64.59                         0          0        214                                      14 2.041             
   otter    64.53                         0          0         40                                   35.38 3.273             
             ltpb  ltps  ltrunc  ltrunclen   ppl  token_acc  token_em  total_train_updates  tpb   tps   ups  
   all   

21:58:49 | running eval: valid
21:59:00 | eval completed in 11.80s
21:59:00 | valid:
             accuracy  bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss        lr  ltpb  \
   all              0  .02339 53.69 635.2 654.8       0          0 14.54  171 .2391    .2007 14.68 2.487 1.562e-08   190   
   external         0  .02897 62.36                   0          0         44 .2099          15.89 2.765                   
   internal         0  .01781 45.02                   0          0        127 .2683          13.46 2.209                   
             ltps  ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all      195.8       0          0 12.49    .2419      .4750         0                 6312 825.2 850.7  
   external             0          0 15.88    .2055      .4378         0                                   
   internal             0          0 9.105    .2783      .5123         0

21:59:00 | saving mod

21:59:35 | loading dictionary from /home/alex/ParlaiEmely/models/model-runs/blender-internal,external,otter-6,3,1/model.dict
21:59:35 | num words = 54944
21:59:36 | Total parameters: 87,508,992 (87,508,992 trainable)
21:59:36 | Loading existing model params from /home/alex/ParlaiEmely/models/model-runs/blender-internal,external,otter-6,3,1/model
21:59:37 | creating task(s): internal
21:59:37 | Loading ParlAI text data: /home/alex/ParlaiEmely/ParlAI/data/internal/valid.txt
21:59:37 | creating task(s): external
21:59:37 | Loading ParlAI text data: /home/alex/ParlaiEmely/ParlAI/data/external/valid.txt
21:59:37 | running eval: valid
21:59:49 | eval completed in 11.80s
21:59:49 | valid:
             accuracy  bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss        lr  ltpb  \
   all              0  .02339 53.69 635.2 654.9       0          0 14.55  171 .2402    .1933 14.68 2.487 1.562e-08   190   
   external         0  .02897 62.36                   0      

## 4. Blender base + otter and bst

### Datasets with sampling weights:
- internal: 6
- external: 3
- otter: 1
- bst: 1

### Mutators
None

In [7]:
tasks='internal,external,otter,blended_skill_talk'
weights= '6,3'

run_training(tasks=tasks,weights=weights)

22:00:29 | building dictionary first...
22:00:29 | No model with opt yet at: /home/alex/ParlaiEmely/models/model-runs/blender-internal,external,otter,blended_skill_talk-6,3/model(.opt)
22:00:29 | your model is being loaded with opts that do not exist in the model you are initializing the weights with: allow_missing_init_opts: False,download_path: None,loglevel: info,dynamic_batching: None,verbose: False,is_debug: False,datapath: /home/alex/ParlaiEmely/ParlAI/data,eval_dynamic_batching: None,num_workers: 0,max_train_steps: -1,log_every_n_steps: 50,validation_every_n_steps: -1,load_from_checkpoint: True,tensorboard_logdir: None,wandb_log: True,wandb_name: None,wandb_project: parlaiemely,wandb_entity: None,mutators: None,n_encoder_layers: -1,n_decoder_layers: -1,model_parallel: False,beam_block_full_context: True,beam_delay: 30,beam_block_list_filename: None,temperature: 1.0,interactive_mode: False,history_reversed: False,history_add_global_end_token: None,special_tok_lst: None,bpe_vocab:

22:00:31 |     text_truncate: 512
22:00:31 |     topk: 10
22:00:31 |     topp: 0.9
22:00:31 |     truncate: -1
22:00:31 |     update_freq: 1
22:00:31 |     use_reply: label
22:00:31 |     validation_cutoff: 1.0
22:00:31 |     validation_every_n_epochs: 0.25
22:00:31 |     validation_every_n_secs: -1
22:00:31 |     validation_every_n_steps: -1
22:00:31 |     validation_max_exs: 20000
22:00:31 |     validation_metric: ppl
22:00:31 |     validation_metric_mode: min
22:00:31 |     validation_patience: 15
22:00:31 |     validation_share_agent: False
22:00:31 |     variant: xlm
22:00:31 |     verbose: False
22:00:31 |     wandb_entity: None
22:00:31 |     wandb_log: True
22:00:31 |     wandb_name: None
22:00:31 |     wandb_project: parlaiemely
22:00:31 |     warmup_rate: 0.0001
22:00:31 |     warmup_updates: -1
22:00:31 |     weight_decay: None
22:00:31 | Current ParlAI commit: adb7ed134aec01437ef8d4e6bf450827fd0fbdc2
22:00:31 | creating task(s): internal,external,otter,blended_skill_talk
22

22:00:48 | training...
22:00:54 | time:23s total_exs:800 total_steps:50 epochs:0.03
                       clen  clip  ctpb  ctps   ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gpu_mem  llen  loss    lr  \
   all                81.62 .9800  1345 11450 .0007813     .06797 136.2  800             18186    .4414 21.25 2.846 1e-06   
   blended_skill_talk 87.96                          0          0        161                            17.68 2.274         
   external           85.63                          0          0        248                            14.23 3.007         
   internal           84.75                    .003125      .2719        320                            14.33 2.665         
   otter              68.15                          0          0         71                            38.75 3.437         
                       ltpb  ltps  ltrunc  ltrunclen   ppl  token_acc  token_em  total_train_updates  tpb   tps   ups  
   all                  272  2315  .01056     

22:01:01 | time:30s total_exs:1600 total_steps:100 epochs:0.06
                       clen  clip  ctpb  ctps  ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gnorm  gpu_mem  llen  loss  \
   all                86.22     1  1362 10523 .002463      .3768 123.7  800              8192   11.1    .5350 20.78 2.814   
   blended_skill_talk 96.46                         0          0        175                                   17.21 2.266   
   external           88.15                   .009852      1.507        203                                   14.56 2.937   
   internal           79.41                         0          0        357                                    14.1 2.609   
   otter              80.83                         0          0         65                                   37.25 3.443   
                         lr  ltpb  ltps  ltrunc  ltrunclen   ppl  token_acc  token_em  total_train_updates  tpb   tps  ups  
   all                1e-06   268  2071 .003846     .09231 18.

22:01:31 | saving model checkpoint: /home/alex/ParlaiEmely/models/model-runs/blender-internal,external,otter,blended_skill_talk-6,3/model.checkpoint
22:01:31 | Saving dictionary to /home/alex/ParlaiEmely/models/model-runs/blender-internal,external,otter,blended_skill_talk-6,3/model.checkpoint.dict
22:01:38 | time:67s total_exs:6400 total_steps:400 epochs:0.22
                       clen  clip  ctpb  ctps  ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gnorm  gpu_mem  llen  loss  \
   all                87.93     1  1411  9029       0          0 102.4  800              8192   10.7    .3704 18.92 2.693   
   blended_skill_talk 93.23                         0          0        218                                   17.45 2.311   
   external           87.57                         0          0        242                                   14.45 2.837   
   internal           85.35                         0          0        292                                   14.39 2.449   
   otter     

...

22:44:18 | time:2627s total_exs:262496 total_steps:16406 epochs:9.20
                       clen  clip  ctpb  ctps  ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gnorm  gpu_mem  llen  loss  \
   all                  102     1  1449 10682 .001244     .03234 117.9  800              8192  9.966    .4878 19.39 2.346   
   blended_skill_talk 99.19                   .004975      .1294        201                                   20.33 2.525   
   external           87.48                         0          0        226                                   14.65 1.828   
   internal           81.05                         0          0        330                                   14.18 1.732   
   otter              140.3                         0          0         43                                    28.4   3.3   
                            lr  ltpb  ltps  ltrunc  ltrunclen   ppl  token_acc  token_em  total_train_updates  tpb   tps   ups  
   all                1.25e-07 265.9  1960       0  

22:45:03 | time:2672s total_exs:266432 total_steps:16652 epochs:9.34
                       clen  clip  ctpb  ctps  ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gnorm  gpu_mem  llen  loss  \
   all                94.24     1  1497 13060  .00431      .6024 139.6  800              8192  10.37    .4711 19.37 2.272   
   blended_skill_talk 107.7                    .01724      2.409        232                                   18.54 2.413   
   external           90.21                         0          0        196                                   14.92 1.877   
   internal           87.11                         0          0        300                                   14.27  1.75   
   otter              91.96                         0          0         72                                   29.75 3.049   
                            lr  ltpb  ltps  ltrunc  ltrunclen   ppl  token_acc  token_em  total_train_updates  tpb   tps   ups  
   all                1.25e-07 272.1  2374 .006944  

22:45:41 | time:2710s total_exs:271168 total_steps:16948 epochs:9.50
                       clen  clip  ctpb  ctps  ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gnorm  gpu_mem  llen  loss  \
   all                87.82     1  1348 11898 .006232      .5052 141.2  736              8192  10.15    .4624 18.85  2.25   
   blended_skill_talk 94.95                         0          0        154                                   16.94 2.431   
   external           81.82                   .004926      .2808        203                                   14.35 1.832   
   internal           79.62                         0          0        329                                   14.17 1.706   
   otter              94.88                     .0200       1.74         50                                   29.96  3.03   
                            lr  ltpb  ltps  ltrunc  ltrunclen   ppl  token_acc  token_em  total_train_updates  tpb   tps   ups  
   all                1.25e-07 253.9  2241       0  

22:46:21 | time:2749s total_exs:274368 total_steps:17148 epochs:9.61
                       clen  clip  ctpb  ctps   ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gnorm  gpu_mem  llen  loss  \
   all                97.27     1  1482 11101 .0008361     .01589 119.9  800              4096  10.01    .5349 23.97  2.33   
   blended_skill_talk 98.83                          0          0        263                                    17.9 2.372   
   external           88.78                          0          0        196                                   16.07  1.84   
   internal           86.57                    .003344     .06355        299                                   14.68 1.841   
   otter              114.9                          0          0         42                                   47.24 3.268   
                            lr  ltpb  ltps  ltrunc  ltrunclen   ppl  token_acc  token_em  total_train_updates  tpb   tps   ups  
   all                1.25e-07 281.6  2110  .0

22:46:51 | running eval: valid
22:47:03 | eval completed in 12.11s
22:47:03 | valid:
             accuracy  bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss       lr  ltpb  ltps  \
   all              0  .02029 53.69 635.2   638       0          0 14.17  171 .2315    .2003 14.68 2.482 1.25e-07   190 190.8   
   external         0  .02364 62.36                   0          0         44 .1943          15.89 2.771                        
   internal         0  .01695 45.02                   0          0        127 .2687          13.46 2.194                        
             ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all            0          0 12.47    .2363      .4748         0                17394 825.2 828.8  
   external       0          0 15.97    .1950      .4349         0                                   
   internal       0          0 8.969    .2776      .5146         0

22:47:04 | saving model c

# Mutator runs below

Mutators change the dataset

## 5. Blender base +  word_shuffle

### Datasets with sampling weights:
- internal: 6
- external: 3


### Mutators
- word_shuffle


In [8]:
tasks='internal,external'
weights= '6,3'
mutators = 'word_shuffle'

run_training(tasks=tasks, weights=weights, mutators=mutators)

22:48:00 | building dictionary first...
22:48:00 | No model with opt yet at: /home/alex/ParlaiEmely/models/model-runs/blender-internal,external-6,3-word_shuffle/model(.opt)
22:48:00 | your model is being loaded with opts that do not exist in the model you are initializing the weights with: allow_missing_init_opts: False,download_path: None,loglevel: info,dynamic_batching: None,verbose: False,is_debug: False,datapath: /home/alex/ParlaiEmely/ParlAI/data,eval_dynamic_batching: None,num_workers: 0,max_train_steps: -1,log_every_n_steps: 50,validation_every_n_steps: -1,load_from_checkpoint: True,tensorboard_logdir: None,wandb_log: True,wandb_name: None,wandb_project: parlaiemely,wandb_entity: None,mutators: word_shuffle,n_encoder_layers: -1,n_decoder_layers: -1,model_parallel: False,beam_block_full_context: True,beam_delay: 30,beam_block_list_filename: None,temperature: 1.0,interactive_mode: False,history_reversed: False,history_add_global_end_token: None,special_tok_lst: None,bpe_vocab: Non

22:48:01 |     topk: 10
22:48:01 |     topp: 0.9
22:48:01 |     truncate: -1
22:48:01 |     update_freq: 1
22:48:01 |     use_reply: label
22:48:01 |     validation_cutoff: 1.0
22:48:01 |     validation_every_n_epochs: 0.25
22:48:01 |     validation_every_n_secs: -1
22:48:01 |     validation_every_n_steps: -1
22:48:01 |     validation_max_exs: 20000
22:48:01 |     validation_metric: ppl
22:48:01 |     validation_metric_mode: min
22:48:01 |     validation_patience: 15
22:48:01 |     validation_share_agent: False
22:48:01 |     variant: xlm
22:48:01 |     verbose: False
22:48:01 |     wandb_entity: None
22:48:01 |     wandb_log: True
22:48:01 |     wandb_name: None
22:48:01 |     wandb_project: parlaiemely
22:48:01 |     warmup_rate: 0.0001
22:48:01 |     warmup_updates: -1
22:48:01 |     weight_decay: None
22:48:01 | Current ParlAI commit: adb7ed134aec01437ef8d4e6bf450827fd0fbdc2
22:48:01 | creating task(s): internal,external
22:48:01 | Loading ParlAI text data: /home/alex/ParlaiEmely/P

22:48:18 | training...
22:48:20 | time:19s total_exs:256 total_steps:16 epochs:0.26
             clen  clip  ctpb  ctps  ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gnorm  gpu_mem  llen  loss    lr  ltpb  \
   all      55.25     1 896.3  8856       0          0 158.1  256             32768  12.59    .2659 14.08  3.14 1e-06 224.9   
   external 53.28                         0          0         78                                   14.15 3.358               
   internal 57.22                         0          0        178                                   14.01 2.922               
             ltps  ltrunc  ltrunclen   ppl  token_acc  token_em  total_train_updates  tpb   tps   ups  
   all       2222       0          0 23.65      .3658         0                   16 1121 11078 10.04  
   external             0          0 28.72      .3207         0                                        
   internal             0          0 18.57      .4110         0

22:48:20 | creating task(s): in

22:48:40 | running eval: valid
22:48:55 | eval completed in 15.25s
22:48:55 | valid:
             accuracy  bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss    lr  ltpb  ltps  \
   all              0  .00631 53.69 635.2 518.2       0          0 11.51  171 .1426    .2005 14.68 3.013 1e-06   190   155   
   external         0  .00406 62.36                   0          0         44 .1217          15.89 3.242                     
   internal         0  .00856 45.02                   0          0        127 .1635          13.46 2.783                     
             ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all            0          0 20.88    .1411      .3895         0                   32 825.2 673.3  
   external       0          0 25.58    .1177      .3691         0                                   
   internal       0          0 16.17    .1645      .4099         0

22:48:55 | saving model checkpoint: /

22:49:57 | time:116s total_exs:1536 total_steps:96 epochs:1.59
             clen  clip  ctpb  ctps  ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gnorm  gpu_mem  llen  loss    lr  ltpb  \
   all      55.16     1 883.2  9251       0          0 167.6  256             16384  12.26    .2636 14.81 2.951 1e-06   236   
   external 54.99                         0          0         97                                   15.07 3.062               
   internal 55.33                         0          0        159                                   14.55 2.839               
             ltps  ltrunc  ltrunclen   ppl  token_acc  token_em  total_train_updates  tpb   tps   ups  
   all       2472       0          0 19.24      .3967         0                   96 1119 11722 10.48  
   external             0          0 21.38      .3851         0                                        
   internal             0          0  17.1      .4084         0

22:49:57 | running eval: valid
22:50:11 | eval compl

...

23:04:35 | running eval: valid
23:04:47 | eval completed in 11.91s
23:04:47 | valid:
             accuracy  bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss       lr  ltpb  ltps  \
   all              0 .005785 53.69 635.2 672.9       0          0 14.95  171 .1854    .2004 14.68 2.755 1.25e-07   190 201.3   
   external         0 .001318 62.36                   0          0         44 .1561          15.89  3.02                        
   internal         0  .01025 45.02                   0          0        127 .2146          13.46 2.489                        
             ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all            0          0 16.27    .1883      .4349         0                  976 825.2 874.2  
   external       0          0 20.49    .1564      .4020         0                                   
   internal       0          0 12.05    .2202      .4678         0

23:04:47 | saving model c

23:05:37 | running eval: valid
23:05:49 | eval completed in 11.68s
23:05:49 | valid:
             accuracy  bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss       lr  ltpb  ltps  \
   all              0 .008198 53.69 635.2 680.5       0          0 15.12  171 .1869    .2003 14.68 2.764 6.25e-08   190 203.6   
   external         0 .004014 62.36                   0          0         44 .1602          15.89  3.05                        
   internal         0  .01238 45.02                   0          0        127 .2136          13.46 2.477                        
             ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all            0          0 16.51    .1795      .4295         0                 1040 825.2 884.1  
   external       0          0 21.12    .1508      .3934         0                                   
   internal       0          0 11.91    .2081      .4655         0

23:05:49 | saving model c

23:06:38 | running eval: valid
23:06:49 | eval completed in 11.75s
23:06:49 | valid:
             accuracy    bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss       lr  ltpb  \
   all              0   .003207 53.69 635.2 665.9       0          0 14.79  171 .1819    .2004 14.68 2.746 6.25e-08   190   
   external         0 5.012e-06 62.36                   0          0         44 .1502          15.89 3.011                  
   internal         0   .006409 45.02                   0          0        127 .2135          13.46 2.482                  
             ltps  ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb  tps  
   all      199.2       0          0 16.13    .1787      .4338         0                 1104 825.2  865  
   external             0          0  20.3    .1408      .4092         0                                  
   internal             0          0 11.96    .2165      .4585         0

23:06:49 | saving mo

23:07:38 | running eval: valid
23:07:49 | eval completed in 11.55s
23:07:49 | valid:
             accuracy  bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss        lr  ltpb  \
   all              0  .00385 53.69 635.2 674.5       0          0 14.98  171 .1838    .2004 14.68 2.762 3.125e-08   190   
   external         0 .004012 62.36                   0          0         44 .1514          15.89 3.026                   
   internal         0 .003687 45.02                   0          0        127 .2163          13.46 2.498                   
             ltps  ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all      201.7       0          0 16.39    .1766      .4282         0                 1168 825.2 876.2  
   external             0          0 20.62    .1410      .3991         0                                   
   internal             0          0 12.16    .2122      .4573         0

23:07:49 | saving mod

23:08:38 | running eval: valid
23:08:50 | eval completed in 11.80s
23:08:50 | valid:
             accuracy    bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss        lr  ltpb  \
   all              0    .00713 53.69 635.2   668       0          0 14.84  171 .1784    .2003 14.68 2.761 1.562e-08   190   
   external         0 1.428e-05 62.36                   0          0         44 .1431          15.89 3.031                   
   internal         0    .01425 45.02                   0          0        127 .2136          13.46 2.491                   
             ltps  ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all      199.8       0          0 16.39    .1760      .4362         0                 1232 825.2 867.8  
   external             0          0 20.71    .1338      .4063         0                                   
   internal             0          0 12.08    .2182      .4661         0

23:08:50 | sa

## 6. Blender base +  last_turn

### Datasets with sampling weights:
- internal: 6
- external: 3


### Mutators
- last turn

In [9]:
tasks='internal,external'
weights= '6,3'
mutators = 'last_turn'

run_training(tasks=tasks, weights=weights, mutators=mutators)

23:09:46 | building dictionary first...
23:09:46 | No model with opt yet at: /home/alex/ParlaiEmely/models/model-runs/blender-internal,external-6,3-last_turn/model(.opt)
23:09:46 | your model is being loaded with opts that do not exist in the model you are initializing the weights with: allow_missing_init_opts: False,download_path: None,loglevel: info,dynamic_batching: None,verbose: False,is_debug: False,datapath: /home/alex/ParlaiEmely/ParlAI/data,eval_dynamic_batching: None,num_workers: 0,max_train_steps: -1,log_every_n_steps: 50,validation_every_n_steps: -1,load_from_checkpoint: True,tensorboard_logdir: None,wandb_log: True,wandb_name: None,wandb_project: parlaiemely,wandb_entity: None,mutators: last_turn,preserve_context: True,n_encoder_layers: -1,n_decoder_layers: -1,model_parallel: False,beam_block_full_context: True,beam_delay: 30,beam_block_list_filename: None,temperature: 1.0,interactive_mode: False,history_reversed: False,history_add_global_end_token: None,special_tok_lst: No

23:09:47 |     text_truncate: 512
23:09:47 |     topk: 10
23:09:47 |     topp: 0.9
23:09:47 |     truncate: -1
23:09:47 |     update_freq: 1
23:09:47 |     use_reply: label
23:09:47 |     validation_cutoff: 1.0
23:09:47 |     validation_every_n_epochs: 0.25
23:09:47 |     validation_every_n_secs: -1
23:09:47 |     validation_every_n_steps: -1
23:09:47 |     validation_max_exs: 20000
23:09:47 |     validation_metric: ppl
23:09:47 |     validation_metric_mode: min
23:09:47 |     validation_patience: 15
23:09:47 |     validation_share_agent: False
23:09:47 |     variant: xlm
23:09:47 |     verbose: False
23:09:47 |     wandb_entity: None
23:09:47 |     wandb_log: True
23:09:47 |     wandb_name: None
23:09:47 |     wandb_project: parlaiemely
23:09:47 |     warmup_rate: 0.0001
23:09:47 |     warmup_updates: -1
23:09:47 |     weight_decay: None
23:09:47 | Current ParlAI commit: adb7ed134aec01437ef8d4e6bf450827fd0fbdc2
23:09:48 | creating task(s): internal,external
23:09:48 | Loading ParlAI t

23:10:05 | training...
23:10:06 | time:19s total_exs:256 total_steps:16 epochs:0.26
             clen  clip  ctpb  ctps  ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gpu_mem  llen  loss    lr  ltpb  ltps  \
   all      40.08 .9375 636.8  6665       0          0 167.4  256             29696    .2574 15.35 2.923 1e-06 239.4  2505   
   external 40.92                         0          0         86                            16.52 3.167                     
   internal 39.24                         0          0        170                            14.17 2.679                     
             ltrunc  ltrunclen   ppl  token_acc  token_em  total_train_updates   tpb  tps   ups  
   all            0          0 19.15      .4068         0                   16 876.2 9171 10.53  
   external       0          0 23.73      .3786         0                                        
   internal       0          0 14.57      .4350         0



23:10:06 | creating task(s): internal
23:10:06 | Loading ParlAI text data: /home/alex/ParlaiEmely/ParlAI/data/internal/valid.txt
23:10:06 | creating task(s): external
23:10:06 | Loading ParlAI text data: /home/alex/ParlaiEmely/ParlAI/data/external/valid.txt
23:10:06 | running eval: valid
23:10:24 | eval completed in 17.28s
23:10:24 | valid:
             accuracy  bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss    lr  ltpb  ltps  \
   all              0 .003699  38.7 458.4 340.3       0          0 10.48  171 .1694    .2004 14.68 2.855 1e-06   190   141   
   external         0 .005627 44.91                   0          0         44 .1624          15.89 3.125                     
   internal         0  .00177 32.49                   0          0        127 .1764          13.46 2.586                     
             ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all            0          0 18.02    .1744      

23:11:06 | new best ppl: 17.84 (previous best was 18.02)
23:11:06 | saving best valid model: /home/alex/ParlaiEmely/models/model-runs/blender-internal,external-6,3-last_turn/model
23:11:09 | time:81s total_exs:1280 total_steps:80 epochs:1.32
             clen  clip  ctpb  ctps  ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gnorm  gpu_mem  llen  loss    lr  ltpb  \
   all      39.14     1 621.1  7132       0          0 183.7  256             16384  12.91    .2593 15.08  2.92 1e-06 235.9   
   external 40.24                         0          0         91                                   16.23 3.182               
   internal 38.03                         0          0        165                                   13.92 2.657               
             ltps  ltrunc  ltrunclen   ppl  token_acc  token_em  total_train_updates   tpb  tps   ups  
   all       2709       0          0 19.18      .4056         0                   80 856.9 9841 11.49  
   external             0          0  24.1

...

23:41:44 | running eval: valid
23:41:52 | eval completed in 7.08s
23:41:52 | valid:
             accuracy  bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss       lr  ltpb  ltps  \
   all              0  .02824 39.61   519 473.3       0          0 14.59  102 .2545    .2004 14.75 2.579 1.25e-07 222.4 202.8   
   external         0  .03061 46.77                   0          0         22 .2278          15.59 2.848                        
   internal         0  .02587 32.44                   0          0         80 .2812           13.9  2.31                        
             ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all            0          0 13.66    .2633      .4708         0                 2592 741.4 676.1  
   external       0          0 17.25    .2408      .4461         0                                   
   internal       0          0 10.07    .2858      .4955         0

23:41:52 | saving model ch

23:42:27 | running eval: valid
23:42:34 | eval completed in 7.10s
23:42:34 | valid:
             accuracy  bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss       lr  ltpb  ltps  \
   all              0  .02824 39.61   519 471.8       0          0 14.55  102 .2541    .2006 14.75 2.579 6.25e-08 222.4 202.2   
   external         0  .03061 46.77                   0          0         22 .2278          15.59 2.848                        
   internal         0  .02587 32.44                   0          0         80 .2805           13.9  2.31                        
             ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb  tps  
   all            0          0 13.66    .2629      .4708         0                 2656 741.4  674  
   external       0          0 17.26    .2408      .4461         0                                  
   internal       0          0 10.07    .2851      .4955         0

23:42:34 | saving model check

23:43:08 | running eval: valid
23:43:15 | eval completed in 7.13s
23:43:15 | valid:
             accuracy  bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss        lr  ltpb  \
   all              0  .02824 39.61   519 469.8       0          0 14.48  102 .2540    .2004 14.75 2.579 3.125e-08 222.4   
   external         0  .03061 46.77                   0          0         22 .2278          15.59 2.848                   
   internal         0  .02587 32.44                   0          0         80 .2803           13.9  2.31                   
             ltps  ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all      201.3       0          0 13.66    .2629      .4703         0                 2720 741.4 671.1  
   external             0          0 17.25    .2408      .4461         0                                   
   internal             0          0 10.07    .2851      .4946         0

23:43:15 | saving mode

23:43:18 | running eval: valid
23:43:25 | eval completed in 7.09s
23:43:25 | valid:
             accuracy  bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss        lr  ltpb  \
   all              0  .02824 39.61   519 472.4       0          0 14.56  102 .2551    .2005 14.75 2.579 3.125e-08 222.4   
   external         0  .03061 46.77                   0          0         22 .2278          15.59 2.848                   
   internal         0  .02587 32.44                   0          0         80 .2824           13.9  2.31                   
             ltps  ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all      202.4       0          0 13.66    .2637      .4708         0                 2736 741.4 674.8  
   external             0          0 17.26    .2408      .4461         0                                   
   internal             0          0 10.07    .2866      .4955         0

23:43:25 | saving mode

23:44:00 | running eval: valid
23:44:07 | eval completed in 7.05s
23:44:07 | valid:
             accuracy  bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss        lr  ltpb  \
   all              0  .02824 39.61   519 475.7       0          0 14.66  102 .2540    .2004 14.75 2.579 1.562e-08 222.4   
   external         0  .03061 46.77                   0          0         22 .2278          15.59 2.848                   
   internal         0  .02587 32.44                   0          0         80 .2803           13.9  2.31                   
             ltps  ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all      203.8       0          0 13.66    .2629      .4703         0                 2800 741.4 679.5  
   external             0          0 17.25    .2408      .4461         0                                   
   internal             0          0 10.07    .2851      .4946         0

23:44:07 | saving mode

## 7. Blender base + flatten

In [10]:
tasks='internal,external'
weights= '6,3'
mutators = 'flatten'

run_training(tasks=tasks, weights=weights, mutators=mutators)

23:45:04 | building dictionary first...
23:45:04 | No model with opt yet at: /home/alex/ParlaiEmely/models/model-runs/blender-internal,external-6,3-flatten/model(.opt)
23:45:04 | your model is being loaded with opts that do not exist in the model you are initializing the weights with: allow_missing_init_opts: False,download_path: None,loglevel: info,dynamic_batching: None,verbose: False,is_debug: False,datapath: /home/alex/ParlaiEmely/ParlAI/data,eval_dynamic_batching: None,num_workers: 0,max_train_steps: -1,log_every_n_steps: 50,validation_every_n_steps: -1,load_from_checkpoint: True,tensorboard_logdir: None,wandb_log: True,wandb_name: None,wandb_project: parlaiemely,wandb_entity: None,mutators: flatten,n_encoder_layers: -1,n_decoder_layers: -1,model_parallel: False,beam_block_full_context: True,beam_delay: 30,beam_block_list_filename: None,temperature: 1.0,interactive_mode: False,history_reversed: False,history_add_global_end_token: None,special_tok_lst: None,bpe_vocab: None,bpe_merg

23:45:05 |     topk: 10
23:45:05 |     topp: 0.9
23:45:05 |     truncate: -1
23:45:05 |     update_freq: 1
23:45:05 |     use_reply: label
23:45:05 |     validation_cutoff: 1.0
23:45:05 |     validation_every_n_epochs: 0.25
23:45:05 |     validation_every_n_secs: -1
23:45:05 |     validation_every_n_steps: -1
23:45:05 |     validation_max_exs: 20000
23:45:05 |     validation_metric: ppl
23:45:05 |     validation_metric_mode: min
23:45:05 |     validation_patience: 15
23:45:05 |     validation_share_agent: False
23:45:05 |     variant: xlm
23:45:05 |     verbose: False
23:45:05 |     wandb_entity: None
23:45:05 |     wandb_log: True
23:45:05 |     wandb_name: None
23:45:05 |     wandb_project: parlaiemely
23:45:05 |     warmup_rate: 0.0001
23:45:05 |     warmup_updates: -1
23:45:05 |     weight_decay: None
23:45:05 | Current ParlAI commit: adb7ed134aec01437ef8d4e6bf450827fd0fbdc2
23:45:05 | creating task(s): internal,external
23:45:05 | Loading ParlAI text data: /home/alex/ParlaiEmely/P

23:45:23 | training...
23:45:24 | time:19s total_exs:256 total_steps:16 epochs:0.26
             clen  clip  ctpb  ctps  ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gnorm  gpu_mem  llen  loss    lr  ltpb  \
   all      51.15     1 823.3  8775       0          0 170.5  256             32768  12.37    .2710 14.82 2.857 1e-06 236.2   
   external 50.28                         0          0         83                                   14.96 2.944               
   internal 52.02                         0          0        173                                   14.67  2.77               
             ltps  ltrunc  ltrunclen   ppl  token_acc  token_em  total_train_updates  tpb   tps   ups  
   all       2518       0          0 17.48      .4039         0                   16 1060 11293 10.78  
   external             0          0    19      .3905         0                                        
   internal             0          0 15.97      .4173         0

23:45:24 | creating task(s): in

23:45:58 | running eval: valid
23:46:08 | eval completed in 9.88s
23:46:08 | valid:
             accuracy  bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss    lr  ltpb  ltps  \
   all              0 .006064 39.61   519 347.8       0          0 10.72  102 .1786    .2007 14.75 2.857 1e-06 222.4 149.1   
   external         0 .007206 46.77                   0          0         22 .1675          15.59 3.143                     
   internal         0 .004923 32.44                   0          0         80 .1897           13.9 2.572                     
             ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all            0          0 18.13    .1870      .4224         0                   48 741.4 496.9  
   external       0          0 23.16    .1875      .3907         0                                   
   internal       0          0 13.09    .1865      .4541         0

23:46:08 | saving model checkpoint: /h

23:46:50 | running eval: valid
23:46:59 | eval completed in 9.14s
23:46:59 | valid:
             accuracy  bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss    lr  ltpb  ltps  \
   all              0  .01402 39.61   519 375.8       0          0 11.59  102 .2273    .2006 14.75 2.811 5e-07 222.4   161   
   external         0  .02047 46.77                   0          0         22 .2235          15.59 3.096                     
   internal         0 .007572 32.44                   0          0         80 .2312           13.9 2.526                     
             ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all            0          0 17.31    .2303      .4294         0                  112 741.4 536.8  
   external       0          0 22.11    .2395      .3965         0                                   
   internal       0          0  12.5    .2210      .4622         0

23:46:59 | saving model checkpoint: /h

...

00:42:10 | saving model checkpoint: /home/alex/ParlaiEmely/models/model-runs/blender-internal,external-6,3-flatten/model.checkpoint
00:42:11 | did not beat best ppl: 13.7329 impatience: 1
00:42:11 | saving model checkpoint: /home/alex/ParlaiEmely/models/model-runs/blender-internal,external-6,3-flatten/model.checkpoint
00:42:14 | time:3428s total_exs:74496 total_steps:4656 epochs:77.04
             clen  clip  ctpb  ctps  ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gnorm  gpu_mem  llen  loss        lr  \
   all      39.96     1 638.8  6781       0          0 169.8  256              4096  10.16    .2595 15.66 2.166 1.562e-08   
   external 40.07                         0          0         83                                   17.43 2.304             
   internal 39.86                         0          0        173                                   13.89 2.028             
             ltpb  ltps  ltrunc  ltrunclen   ppl  token_acc  token_em  total_train_updates   tpb  tps   ups  
  

00:42:52 | saving model checkpoint: /home/alex/ParlaiEmely/models/model-runs/blender-internal,external-6,3-flatten/model.checkpoint
00:42:53 | did not beat best ppl: 13.7329 impatience: 5
00:42:55 | time:3469s total_exs:75520 total_steps:4720 epochs:78.10
             clen  clip  ctpb  ctps  ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gnorm  gpu_mem  llen  loss        lr  \
   all      41.82     1 658.2  7095       0          0 172.4  256              4096  10.34    .2378 14.45 2.126 1.562e-08   
   external 44.07                         0          0         89                                    14.6 2.194             
   internal 39.58                         0          0        167                                   14.31 2.059             
             ltpb  ltps  ltrunc  ltrunclen   ppl  token_acc  token_em  total_train_updates   tpb  tps   ups  
   all      230.6  2485       0          0 8.404      .5419         0                 4720 888.8 9580 10.78  
   external             

00:43:33 | saving model checkpoint: /home/alex/ParlaiEmely/models/model-runs/blender-internal,external-6,3-flatten/model.checkpoint
00:43:35 | did not beat best ppl: 13.7329 impatience: 9
00:43:36 | time:3511s total_exs:76544 total_steps:4784 epochs:79.16
             clen  clip  ctpb  ctps  ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gnorm  gpu_mem  llen  loss        lr  \
   all      39.77     1 628.4  6516       0          0 165.9  256              4096  10.11    .2556  14.6 2.022 1.562e-08   
   external 41.43                         0          0         90                                   14.81 1.985             
   internal  38.1                         0          0        166                                    14.4 2.059             
             ltpb  ltps  ltrunc  ltrunclen   ppl  token_acc  token_em  total_train_updates   tpb  tps   ups  
   all      232.7  2413       0          0 7.559      .5325   .003012                 4784 861.1 8929 10.38  
   external             

00:44:14 | saving model checkpoint: /home/alex/ParlaiEmely/models/model-runs/blender-internal,external-6,3-flatten/model.checkpoint
00:44:16 | did not beat best ppl: 13.7329 impatience: 13
00:44:16 | saving model checkpoint: /home/alex/ParlaiEmely/models/model-runs/blender-internal,external-6,3-flatten/model.checkpoint
00:44:19 | time:3553s total_exs:77568 total_steps:4848 epochs:80.22
             clen  clip  ctpb  ctps  ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gnorm  gpu_mem  llen  loss        lr  \
   all      39.49     1 632.8  6909       0          0 174.7  256              4096  10.62    .2595 13.88 2.062 1.562e-08   
   external 39.28                         0          0         93                                   14.83 2.147             
   internal 39.71                         0          0        163                                   12.93 1.978             
             ltpb  ltps  ltrunc  ltrunclen   ppl  token_acc  token_em  total_train_updates   tpb  tps   ups  
 

00:44:51 | creating task(s): internal
00:44:51 | Loading ParlAI text data: /home/alex/ParlaiEmely/ParlAI/data/internal/test.txt
00:44:51 | creating task(s): external
00:44:51 | Loading ParlAI text data: /home/alex/ParlaiEmely/ParlAI/data/external/test.txt
00:44:51 | running eval: test
00:45:03 | eval completed in 12.00s
00:45:03 | test:
             accuracy  bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss        lr  ltpb  \
   all              0  .01769 53.69 635.2 648.7       0          0 14.41  171 .2260    .1934 14.68 2.555 1.562e-08   190   
   external         0  .01406 62.36                   0          0         44 .1901          15.89 2.851                   
   internal         0  .02132 45.02                   0          0        127 .2618          13.46 2.258                   
             ltps  ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all        194       0          0 13.44    .2296      

## 8. Blender base + mixed mutators

### Datasets with sampling weights:
- internal: 6
- external: 3


### Mutators
- None
- word_shuffle
- flatten
- last_turn

In [11]:
tasks = 'internal,external'
weights= '2,1'
mutators = 'word_shuffle,flatten,last_turn'

run_training(tasks=tasks, weights=weights, mutators=mutators)

00:45:30 | building dictionary first...
00:45:30 | No model with opt yet at: /home/alex/ParlaiEmely/models/model-runs/blender-internal,external-2,1-word_shuffle,flatten,last_turn/model(.opt)
00:45:30 | your model is being loaded with opts that do not exist in the model you are initializing the weights with: allow_missing_init_opts: False,download_path: None,loglevel: info,dynamic_batching: None,verbose: False,is_debug: False,datapath: /home/alex/ParlaiEmely/ParlAI/data,eval_dynamic_batching: None,num_workers: 0,max_train_steps: -1,log_every_n_steps: 50,validation_every_n_steps: -1,load_from_checkpoint: True,tensorboard_logdir: None,wandb_log: True,wandb_name: None,wandb_project: parlaiemely,wandb_entity: None,mutators: word_shuffle,flatten,last_turn,preserve_context: True,n_encoder_layers: -1,n_decoder_layers: -1,model_parallel: False,beam_block_full_context: True,beam_delay: 30,beam_block_list_filename: None,temperature: 1.0,interactive_mode: False,history_reversed: False,history_add_

00:45:32 |     task: internal,external
00:45:32 |     temperature: 1.0
00:45:32 |     tensorboard_log: True
00:45:32 |     tensorboard_logdir: None
00:45:32 |     text_truncate: 512
00:45:32 |     topk: 10
00:45:32 |     topp: 0.9
00:45:32 |     truncate: -1
00:45:32 |     update_freq: 1
00:45:32 |     use_reply: label
00:45:32 |     validation_cutoff: 1.0
00:45:32 |     validation_every_n_epochs: 0.25
00:45:32 |     validation_every_n_secs: -1
00:45:32 |     validation_every_n_steps: -1
00:45:32 |     validation_max_exs: 20000
00:45:32 |     validation_metric: ppl
00:45:32 |     validation_metric_mode: min
00:45:32 |     validation_patience: 15
00:45:32 |     validation_share_agent: False
00:45:32 |     variant: xlm
00:45:32 |     verbose: False
00:45:32 |     wandb_entity: None
00:45:32 |     wandb_log: True
00:45:32 |     wandb_name: None
00:45:32 |     wandb_project: parlaiemely
00:45:32 |     warmup_rate: 0.0001
00:45:32 |     warmup_updates: -1
00:45:32 |     weight_decay: None
0

00:45:49 | training...
00:45:51 | time:19s total_exs:256 total_steps:16 epochs:0.26
             clen  clip  ctpb  ctps  ctrunc  ctrunclen  exps  exs  fp16_loss_scalar  gnorm  gpu_mem  llen  loss    lr  ltpb  \
   all      53.54     1 851.8  8734       0          0   164  256             32768  12.28    .2710 15.17  3.09 1e-06 236.7   
   external 54.28                         0          0         76                                   16.11 3.321               
   internal  52.8                         0          0        180                                   14.24 2.859               
             ltps  ltrunc  ltrunclen   ppl  token_acc  token_em  total_train_updates  tpb   tps   ups  
   all       2427       0          0 22.56      .3836         0                   16 1088 11160 10.32  
   external             0          0 27.68      .3578         0                                        
   internal             0          0 17.45      .4093         0

00:45:51 | creating task(s): in

00:46:35 | running eval: valid
00:46:44 | eval completed in 8.92s
00:46:44 | valid:
             accuracy    bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss    lr  ltpb  ltps  \
   all              0 1.637e-06 39.61   519 391.9       0          0 12.08  102 .1363    .2006 14.75 3.115 1e-06 222.4 167.9   
   external         0 1.892e-08 46.77                   0          0         22 .1049          15.59 3.405                     
   internal         0 3.255e-06 32.44                   0          0         80 .1678           13.9 2.826                     
             ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all            0          0 23.49    .1438      .3825         0                   64 741.4 559.8  
   external       0          0 30.11    .1241      .3586         0                                   
   internal       0          0 16.87    .1634      .4065         0

00:46:44 | saving model checkp

00:47:22 | running eval: valid
00:47:30 | eval completed in 8.48s
00:47:30 | valid:
             accuracy    bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss    lr  ltpb  ltps  \
   all              0 1.067e-05 39.61   519 407.5       0          0 12.56  102 .1539    .2005 14.75 3.071 5e-07 222.4 174.6   
   external         0 1.777e-05 46.77                   0          0         22 .1485          15.59 3.339                     
   internal         0 3.577e-06 32.44                   0          0         80 .1594           13.9 2.803                     
             ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all            0          0 22.34    .1544      .3933         0                  128 741.4 582.2  
   external       0          0 28.19    .1556      .3703         0                                   
   internal       0          0 16.49    .1533      .4164         0

00:47:30 | saving model checkp

00:48:07 | running eval: valid
00:48:15 | eval completed in 7.93s
00:48:15 | valid:
             accuracy    bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss      lr  ltpb  \
   all              0   .002922 39.61   519 430.9       0          0 13.28  102 .1722    .2005 14.75 3.036 2.5e-07 222.4   
   external         0 2.562e-06 46.77                   0          0         22 .1542          15.59 3.303                 
   internal         0   .005842 32.44                   0          0         80 .1902           13.9 2.769                 
             ltps  ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all      184.6       0          0 21.58    .1673      .3980         0                  192 741.4 615.5  
   external             0          0 27.21    .1508      .3761         0                                   
   internal             0          0 15.94    .1838      .4200         0

00:48:15 | saving mode

00:48:53 | running eval: valid
00:49:00 | eval completed in 7.71s
00:49:00 | valid:
             accuracy    bleu-4  clen  ctpb  ctps  ctrunc  ctrunclen  exps  exs    f1  gpu_mem  llen  loss      lr  ltpb  \
   all              0   .002468 39.61   519 456.5       0          0 14.07  102 .1913    .2005 14.75 3.056 2.5e-07 222.4   
   external         0 1.288e-05 46.77                   0          0         22 .1756          15.59 3.374                 
   internal         0   .004923 32.44                   0          0         80 .2069           13.9 2.738                 
             ltps  ltrunc  ltrunclen   ppl  rouge_L  token_acc  token_em  total_train_updates   tpb   tps  
   all      195.6       0          0 22.33    .1985      .3899         0                  256 741.4 652.1  
   external             0          0  29.2    .1915      .3644         0                                   
   internal             0          0 15.45    .2056      .4155         0

00:49:00 | saving mode